# Working with accent data in the Mozilla Common Voice dataset 

The purpose of this Python Jupyter notebook is to provide some worked examples of how you might explore accent data in the Common Voice dataset. 



## Index of notebook contents 

To make this notebook easier to navigate, each section is indexed below. 

* [Background information on demographic data in Common Voice](#Background)
* [Preparation steps and importing modules](#PreparationSteps) - including the `requirements.txt` you should run if using this notebook. 
* [The Accent and AccentDescriptor classes we will use in the notebook](#Classes)
* [Preparing data from the Common Voice TSV file](#PreparingData)
* [Extracting accent information for data visualisation](#AccentExtraction)
* [Determine which accents are predetermined for selection in the Common Voice profile screen](#PreDetermined)
* [Add Descriptors to each Accent](#Descriptors)

---
<a id='Background'></a>
## Background information on demographic data in Common Voice 

Before you start working with accent data in Common Voice, there is background information you should know about the data structures in the Common Voice datasets, and how accents have been represented. 

### The ability to choose whether or not to specify demographic information 

Data contributors can contribute voice data to Common Voice with our without logging in to the platform. If a data contributor is not logged in, the utterances they record contain no demographic metadata information, such as the gender, age range or accent of the speaker. If the data contributor _does_ log in, then they can choose whether to specify demographic information in their profile. Part of the demographic information can include specifying which accent(s) they speak with. 


Since mid 2021, data contributors to the Common Voice dataset have been able to self-specify descriptors for their accents. 

The purpose of this script is to get demographic details from an MCV downloaded dataset. 
This informs decision making around, for example, how much of the data in a particular language, has demographic details, and if so, what they are. 

---
<a id='PreparationSteps'></a>

## Preparation steps and importing the modules we will use 

@TODO 

make a `requirements.txt` file to install all the dependencies. 

* pandas 


In [1]:
# imports go here 

# io 
import io

# os for file handling 
import os 

# pandas 
import pandas as pd

# regular expressions 
import re

# json 
import json

# string handling for isascii
import string 

# pretty print 
import pprint
pp = pprint.PrettyPrinter(indent=4)

# reload = because I'm developing the CVaccents module as I go, I want to reload it each time so it doesn't cache
from importlib import reload

# copy = for using deepcopy()
import copy

In [2]:
# set the version number so that we can differentiate files, such as JSON, that are produced. 

dataset_release_version = 14
JSON_data_dir = 'JSON-data-files'
language_code = 'ar'

# specify the filenames for the JSON output

accents_filename = JSON_data_dir + '/' + 'all_accents' + '_' + str(dataset_release_version) + '_' + language_code + '.json'
links_filename = JSON_data_dir + '/' + 'accent_edges' + '_' +  str(dataset_release_version) + '_' + language_code + '.json'

---
<a id='Classes'></a>
## Accent, AccentDescriptor and AccentCollection classes used for manipulation

In [3]:
## Accent class and AccentDescriptor class 

# these are classes I defined for accent handling
import cvaccents as cva

# do an explicit reload as I'm still working on the classes 
#reload(cva)

# prove that my DocStrings are useful
# they are good, so I am suppressing output while I work through the rest of the doc. 

#print('Module docstring is: \n', cva.__doc__)
#print('---')
#print('Accent docstring is: \n', cva.Accent.__doc__)
#print('---')
#print('AccentDescriptor docstring is: \n', cva.AccentDescriptor.__doc__)
#print('---')
#print('AccentCollection docstring is: \n', cva.AccentDescriptor.__doc__)
#print('---')

---
<a id='PreparingData'></a>
## Preparing the data from the Common Voice dataset TSV file

Here, we extract data from the TSV file, and use `pandas` to perform manipulations on the dataset, such as removing rows that do not contain accent metadata. 

In [4]:
# You will need to download the CV corpus somewhere, or at least have the validated.tsv file available. 

# I have found that the aria2c downloader works very well for large downloads. 
# https://aria2.github.io/

filePath = '../cv-datasets/cv-corpus-14.0-2023-06-23/ar/validated.tsv'

# put it into a DataFrame 
df = pd.read_csv(filePath, sep='\t')

/tmp/ipykernel_1991709/1110582863.py:9: DtypeWarning: Columns (7,10) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(filePath, sep='\t')


In [5]:
df.columns

Index(['client_id', 'path', 'sentence', 'up_votes', 'down_votes', 'age',
       'gender', 'accents', 'variant', 'locale', 'segment'],
      dtype='object')

In [6]:
# We don't want all the columns, as some of them are not useful for the accent analysis 
# Drop the columns we don't want 

df.drop(labels=['path', 'sentence', 'up_votes', 'down_votes', 'segment', 'locale'], axis='columns', inplace=True)
df.columns



Index(['client_id', 'age', 'gender', 'accents', 'variant'], dtype='object')

In [7]:
len(df)

77419

In [8]:
# rows that have accent metadata 
len(df[df['accents'].notna()])

152

In [9]:
display(df)

client_id       age gender  \
0      0237f666c0b4f0779056b7c9289e40c170c6b0974b4214...  twenties   male   
1      053a91dfd8c87629424edbb1a98cebea127137e6532174...       NaN    NaN   
2      073c6a4a1887384a1d6145a3258b7ca48de9f441c1762f...       NaN    NaN   
3      08ea1e4883b0112f794e6cba73552d702ba257721b88df...       NaN    NaN   
4      0aab971eac3eabea7027b19bedcde9f9bf1162f536326d...       NaN    NaN   
...                                                  ...       ...    ...   
77414  3b941765a02cc4e9bdf5d8a99c3e3cc3b1ce3413911116...       NaN    NaN   
77415  3b941765a02cc4e9bdf5d8a99c3e3cc3b1ce3413911116...       NaN    NaN   
77416  3b941765a02cc4e9bdf5d8a99c3e3cc3b1ce3413911116...       NaN    NaN   
77417  3b941765a02cc4e9bdf5d8a99c3e3cc3b1ce3413911116...       NaN    NaN   
77418  3b941765a02cc4e9bdf5d8a99c3e3cc3b1ce3413911116...       NaN    NaN   

      accents  variant  
0         NaN      NaN  
1         NaN      NaN  
2         NaN      NaN  
3         NaN      NaN  
4         NaN      NaN  
...       ...      ...  
77414     NaN      NaN  
77415     NaN      NaN  
77416     NaN      NaN  
77417     NaN      NaN  
77418     NaN      NaN  

[77419 rows x 5 columns]

In [10]:
# remove all the rows where accents are not given (NaN)
# https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.dropna.html
# DataFrame.dropna(*, axis=0, how=_NoDefault.no_default, thresh=_NoDefault.no_default, subset=None, inplace=False)

df.dropna(axis='index', how='any', subset='accents', inplace=True)
len(df)

# this matches the above figure for rows that have accent metadata, so it's a good cross-check

152

In [11]:
# number of unique contributors to the dataset 
len(df['client_id'].unique())

16

In [12]:
# Now that the rows without an accent value have been removed, 
# we want to deduplicate the speaker_id values - because one speaker can speak many utterances
# and we only want to record one accent per speaker 
# and we should end up with the # of rows in the cell above 


# One of the reasons we try and reduce the size of the dataframe 
# first is because this operation is more efficient on a smaller dataframe 
# https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.drop_duplicates.html
# DataFrame.drop_duplicates(subset=None, *, keep='first', inplace=False, ignore_index=False)

df.drop_duplicates(subset='client_id', keep='first', inplace=True)
len(df)

# This length should match the length above 

16

---
<a id='AccentExtraction'></a>
## Extracting the accent data for visualisation 

We have already: 

* Removed any rows where accent data was not available = `NaN`
* De-duplicated based on the `client_id`

So now, we need to extract all the self-styled accents for analysis. 

In [14]:
# They are already unique so we don't need the `.unique` method
arabic_accents = df['accents']

print(len(arabic_accents))

16


In [15]:
"""

The list arabic_accents_list is a list that contains the ORIGINAL accent entries for each speaker. 
In this list, the accents for each speaker are represented as a SINGLE STRING, NOT as a list of strings. 

So, we want to turn this into a LIST of LISTS OF STRINGS, to make it easier for doing data cleaning. 
Each individual string represents one accent descriptor given by a speaker, 
and the list which contains those strings is the grouping of accent descriptors for that speaker. 

We need to preserve the association between accent descriptors - co-references - for later data visualisation. 

"""


arabic_accents_list = [] 

for idx, accent_string in list(enumerate(arabic_accents)): 
    
    # this regex is from 
    # https://stackoverflow.com/questions/26633452/how-to-split-by-commas-that-are-not-within-parentheses
    accent_list=re.split(',\s*(?![^()]*\))', accent_string)
    processed_accent_list = accent_list # we don't want to modify a list we're iterating over
    
    #print ('accent_string is: ', accent_string, ' and accent_list is: ', accent_list)
    for idx_a, accent in list(enumerate(accent_list)): 
        
        #print ('idx_a is: ', idx_a, ' and accent is: ', accent, ' and type of accent is: ', type(accent))
        # Trim any whitespace off the elements, because this makes matching on strings harder later on
        # Strings are immutable in Python, so we have to create another string
        processed_accent_list.remove(accent)
        stripped_accent = accent.strip() 
        processed_accent_list.append(stripped_accent)
        
        # Check for any empty strings and remove them - likely regex artefacts
        if not accent: 
            processed_accent_list.remove(accent)
            
        # Check for any non-Latin characters that we may want to investigate 
        # For example, if one of the accents is garbage or deliberate rubbish
        
        if not accent.isascii(): 
            print('flagging that accent: ', accent, ' is not ASCII encoded, may be in another language')
            
    arabic_accents_list.append(processed_accent_list)

flagging that accent:  مصرية  is not ASCII encoded, may be in another language
flagging that accent:  مصري  is not ASCII encoded, may be in another language
flagging that accent:  فصحى  is not ASCII encoded, may be in another language
flagging that accent:  نجدية  is not ASCII encoded, may be in another language
flagging that accent:  سعودية  is not ASCII encoded, may be in another language
flagging that accent:  خليجية  is not ASCII encoded, may be in another language
flagging that accent:  اللهجة العراقية  is not ASCII encoded, may be in another language
flagging that accent:  الفصحة  is not ASCII encoded, may be in another language
flagging that accent:  عراقي  is not ASCII encoded, may be in another language
flagging that accent:  مصريه  is not ASCII encoded, may be in another language
flagging that accent:  فصحى  is not ASCII encoded, may be in another language


In [16]:
print(len(arabic_accents_list))

16


In [17]:
# only used for debugging, not required, commenting out to reduce size of notebook

#for idx, accent_list in list(enumerate(arabic_accents_list)): 
    #print(idx, accent_list)


---
<a id='Descriptors'></a>
## Add descriptors to each accent

In this section, I apply a set of categories to the accent data. 

**I use a rule-based approach for reproduceability.** 
This could have been done in a spreadsheet, but I'm working in Python so I chose to do it that way. 
This also makes it easier for others applying this work to other languages or to other versions of the dataset. 



### Expand accents that have multiple descriptors in their .name element 

Here, we "break apart" accents that have multiple descriptors in the .name element into **multiple** accents. This is done _programmatically_ to aid in reproduceability. 


### Modify the accent list to expand descriptors while preserving accent co-references

Some of the given accent descriptors contain multiple descriptors in one string. Here, I expand them while maintain co-references. 

For example: 

* `slight Brooklyn accent`  - contains both a City-based descriptor and an accent strength descriptor. 
* `United States English combined with European English` - contains both a national descriptor and a supranational descriptor. 



It's easier to do this before we create Accent and AccentDescriptor objects. 

In [18]:
# helper function for the below 

def update_list_coreference(list_to_be_updated, old_entry, new_entry):
    # the accent list is a list of lists so we need to iterate through each one to find the element to update. 
    
    for idx, accent_list in list(enumerate(list_to_be_updated)):
        
        #print(idx, '- old accent_list is: ', accent_list)
        new_accent_list = accent_list
        
        for accent in accent_list:  
            match = False
            #print ('accent is: ', accent, ' and old_entry is: ', old_entry)
            
            if accent == old_entry:
                match = True 
                #print('accent is: ', accent, ' and old_entry is: ', old_entry, 'and new_entry is: ', new_entry)
                #print('accent is: ', accent, ' which matches ', old_entry)
                new_accent_list.remove(old_entry)
                
                for entry in new_entry: # there may be more than one
                    new_accent_list.append(entry)
                    #print('appending new entry: ', entry)
                
            if match: 
                #print ('processed ', old_entry, ' to be ', new_entry, ' and the old accent list is: ', accent_list, ' and the new accent list is: ', new_accent_list)
                if (idx % 1000 == 0): 
                    print(' . ' + str(idx), end='') # trying to reduce size of notebook

        # recreate the list from keys, this removes duplicates
        # for example, a duplicate may be created due to normalisation or merger of accents 
        # run through a filter to remove empty list elements
        new_accent_list = list(dict.fromkeys(filter(None, new_accent_list)))
        
        #print('new_accent_list is: ', new_accent_list)
        #print('---')
        
        #print('removing: ', accent_list)
        list_to_be_updated.remove(accent_list)
        #print('appending: ', newlist)
        list_to_be_updated.append(new_accent_list)
        
    
    return(list_to_be_updated)

In [20]:
# no accents to split 
#arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               #'south German / Swiss accent', 
                                               #['South German', 'Swiss'])




### Normalize closely related accent descriptors - merge them 

There are several closely related accent descriptors, and here I merge them. 

The principles I use are: 
    
* Accents are merged where there are spelling variations 
* Accents are merged where the accent has a region descriptor with our without 'accent' - such as "French" and "French accent"
* Where a country or language descriptor and demonym are closely equivalent - "Germany" and "German"

Accents are not merged where: 

* One accent descriptor is more granular than another - "London" and "South London" are not merged. 

In [36]:
# I can just use the same function

## There will be others as we put them into objects / classes

# 'نجدية' - Najdi Arabic - sub-regional of Saudi Arabia 
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'نجدية',
                                               ['Najdi Arabic'])

# 'Modern Standard Arabic' - Canonical - this is what Fusha or al-Fusha should be 
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'Standard',
                                               ['Modern Standard Arabic - Fusha'])
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'الفصحة',
                                               ['Modern Standard Arabic - Fusha'])
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'فصحى',
                                               ['Modern Standard Arabic - Fusha'])
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'Fusha',
                                               ['Modern Standard Arabic - Fusha'])
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'Modern Standard Arabic',
                                               ['Modern Standard Arabic - Fusha'])


# Egyptian 
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'مصريه',
                                               ['Egyptian'])
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'مصرية',
                                              ['Egyptian'])
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'مصري',
                                              ['Egyptian'])

# Iraqi
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'عراقي',
                                              ['Iraqi'])
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'اللهجة العراقية',
                                              ['Iraqi'])

                                               
# Saudi Arabian
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'سعودية',
                                              ['Saudi Arabian'])
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'Saudi Arabia',
                                              ['Saudi Arabian'])

# Gulf Arabic 
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'خليجية',
                                              ['Gulf Arabic'])

# Darija - Moroccan Arabic 
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'darija',
                                              ['Moroccan Arabic'])

# Fluency markers 
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'fluent Arabic',
                                              ['fluent'])
arabic_accents_list = update_list_coreference(arabic_accents_list, 
                                               'Exellent',
                                              ['excellent'])


In [37]:
# only needed for debugging
# pp.pprint(arabic_accents_list)


## Extract unique accents from the list of normalised accents into a Dict of Accent objects for easier manipulation

In [38]:
# build a dict of each unique accent using an Accent object for each object. 

ratio_display = 120 # to stop the browser crashing 

AccentDict = {}
i = 0; 

# the arabic_accents_list is now normalised, merged etc so this is straightforward 
for accent_list in arabic_accents_list:
    for accent in accent_list: 
        
        i +=1
        match = False 
        count = 0
        
        #if (i%ratio_display ==0): # only show the 100th 
            #print('')
            #print('---')
            #print('now processing: ', accent, ' - ', i)
            #print('---')
        
        # is this accent in our dict - if not, add it in 
        
        for item in AccentDict.items() : # Each item should be an Accent object 
            
            # (self, id=0, name="Accent Name", count=0, locale=None, descriptors=None):
            #pp.pprint(item[1].__str__())
            
            #if (i%ratio_display ==0): # only show the 100th 
                #print('item is: ', item)
                #print(type(item))
                #print('now checking match for: item:', item[1], ' and accent: ', accent)
            
            if (item[1].name == accent) : # update the count
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('---')
                    #print('match is True')
                    #print('---')
                    
                match = True 
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('accent count was: ', item[1].count)
                
                # update the count of the accent 
                item[1].count+=1
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('accent count is now: ', item[1].count)
                
                
        # this match loop has to be outside the for: loop above 
        # because if we add items to the dict inside the loop
        # then it will not run - because there are zero items in the dict to begin with 
        
        if (not match) :   
            
            # (self, id=0, name="Accent Name", count=0, locale=None, descriptors=None):
            AccentDict[i] = cva.Accent(i, accent, 1, 'en', None, False) 
                


In [39]:
# do an explicit reload as I'm still working on the classes 
#reload(cva)

all_accents = cva.AccentCollection(AccentDict)

In [40]:
print(all_accents.total())

12


In [41]:
# only for debugging
all_accents.__str__()

'id is 1, name is Syrian, count is 3, locale is en, descriptors are None, predetermined is False. id is 2, name is Modern Standard Arabic - Fusha, count is 7, locale is en, descriptors are None, predetermined is False. id is 4, name is Moroccan Arabic, count is 1, locale is en, descriptors are None, predetermined is False. id is 7, name is excellent, count is 1, locale is en, descriptors are None, predetermined is False. id is 8, name is Egyptian, count is 3, locale is en, descriptors are None, predetermined is False. id is 9, name is nasal breathing issues, count is 1, locale is en, descriptors are None, predetermined is False. id is 12, name is Najdi Arabic, count is 1, locale is en, descriptors are None, predetermined is False. id is 13, name is Saudi Arabian, count is 2, locale is en, descriptors are None, predetermined is False. id is 14, name is Gulf Arabic, count is 1, locale is en, descriptors are None, predetermined is False. id is 16, name is fluent, count is 1, locale is en,

In [42]:
# do an explicit reload as I'm still working on the classes 
#reload(cva)

all_accents_sortedByCount = all_accents.sortByCount(reverse=True)

for accent in all_accents_sortedByCount.items(): 
    print(accent[1].__str__())
    
# now I am cross-checking to see if there are any other duplicates or accents that should be merged


id is 2, name is Modern Standard Arabic - Fusha, count is 7, locale is en, descriptors are None, predetermined is False.
id is 1, name is Syrian, count is 3, locale is en, descriptors are None, predetermined is False.
id is 8, name is Egyptian, count is 3, locale is en, descriptors are None, predetermined is False.
id is 13, name is Saudi Arabian, count is 2, locale is en, descriptors are None, predetermined is False.
id is 18, name is Iraqi, count is 2, locale is en, descriptors are None, predetermined is False.
id is 9, name is nasal breathing issues, count is 1, locale is en, descriptors are None, predetermined is False.
id is 16, name is fluent, count is 1, locale is en, descriptors are None, predetermined is False.
id is 7, name is excellent, count is 1, locale is en, descriptors are None, predetermined is False.
id is 20, name is North African, count is 1, locale is en, descriptors are None, predetermined is False.
id is 12, name is Najdi Arabic, count is 1, locale is en, descrip

---
<a id='PreDetermined'></a>
## Label the accents that were pre-determined 

Since its inception, Mozilla Common Voice has enabled data contributors to enter demographic age such as age, gender and accent. These associations are not validated in any way, and we don't have any indicator of how accurate they are. Accent _used_ to be represented as an a priori drop-down list, which the contributor could select from. From Common Voice v10, the data contributor can **self-describe** their accent, however, the previous accent list is still presented (so may be more frequently chosen by the data contributor). We need to be able to distinguish these accents visually to help with the exploration. 

```
"splits": {
        "accent": {
          "": 0.51,
          "canada": 0.03,
          "england": 0.08,
          "us": 0.23,
          "indian": 0.07,
          "australia": 0.03,
          "malaysia": 0,
          "newzealand": 0.01,
          "african": 0.01,
          "ireland": 0.01,
          "philippines": 0,
          "singapore": 0,
          "scotland": 0.02,
          "hongkong": 0,
          "bermuda": 0,
          "southatlandtic": 0,
          "wales": 0,
          "other": 0.01
        },

```

The `cv-datasets` splits above have labels for the accents that don't actually match the accent name in the data. So we need to specify the accents that are pre-determined. This is how they appear to the data contributor filling out their profile at: [https://commonvoice.mozilla.org/en/profile/info](https://commonvoice.mozilla.org/en/profile/info)


![Accents as specified on Mozilla Common Voice profile](cv-profile-specify-accent.png)


In [43]:
# create a list of the pre-existing accents 
# this is how they are given in the dataset. 

# TODO: for better maintainability, move this to a list of accents for each language, 
# that can be updated in a separate file, rather than specified here in an adhoc way. 

predetermined_accents_list = ['United States English', 
                         'England English', 
                         'India and South Asia (India, Pakistan, Sri Lanka)', 
                         'Canadian English', 
                         'Australian English', 
                         'Southern African (South Africa, Zimbabwe, Namibia)', 
                         'Irish English', 
                         'Scottish English', 
                         'New Zealand English', 
                         'Hong Kong English', 
                         'Filipino', 
                         'Malaysian English', 
                         'Singaporean English', 
                         'Welsh English', 
                         'West Indies and Bermuda (Bahamas, Bermuda, Jamaica, Trinidad)', 
                         'South Atlantic (Falkland Islands, Saint Helena)']



  

In [44]:
# use the predetermined_accents_list to populate the 'predetermined_status' attribute of each Accent object 
# to do this we use a method on the AccentCollection class

import cvaccents as cva
#reload(cva)

all_accents.updatePredeterminedStatus(predetermined_accents_list, True)
#print(all_accents)


True

---
<a id='AccentDescriptors'></a>

## Create Accent Descriptors and add them to each Accent 

Each Accent can have multiple Accent Descriptors. 

For example the accent `Pronounced German` contains both a _national regional descriptor_ and an _accent strength descriptor_. 

I have used the following principles for Accent Descriptors for English. This should be considered a CodeBook. 

### Geographic Regional Descriptors 

Regional descriptors are where the accent has been specified with reference to a geographic region. 

* `Geographic Region` 

Within this Category, there are several sub-categories: 

* `Country Descriptor` - where the descriptor is a country or a nation-state. 
* `Supranational region descriptor` - where the descriptor is a geographic region that crosses or overlaps multiple countries. An example would be `Slavic`, which refers to an [ethno-linguistic group](https://en.wikipedia.org/wiki/Slavic_languages) that covers several countries in Eastern Europe. 
* `Subnational region descriptor` - where the descriptor is a geographic region that refers to a region within a country's national boundary. An example would be `Midwestern United States`. 
* `City descriptor` - where the descriptor is a geographic region that refers to a city, town or municipality. An example would be `New York City` or `London`. 

One choice I have made here is not to represent areas _within_ cities using a separate Accent Descriptor. Examples here would be `Brooklyn` or `East London` - they have been classified as cities. This is because there are so few of them that it doesn't change the analysis significantly. 

### First or other language descriptor

This refers to Accent Descriptors where the data contributor refers to their accent using a descriptor such as `non-native` or `native speaker`. This is sometimes referred to as `first language (L1)` or `second language (L2)`. Although this _may_ be used to refer to the data contributor's _level of fluency_ in a language, I've chosen not to refer to this as a _level of fluency_ - because even though someone speaks a language as a second or other language, this _does not imply_ their level of fluency specifically. One could speak Mandarin as a second language, but be highly fluent. One could speak French as a second language and be less than proficient. 

* `First or other language` 

### Accent strength descriptor 

This refers to Accent Descriptors where the data contributor refers to their accent using a marker of the strength of the accent. Examples included `pronounced`, `90%` or `slight`. 

* `Accent strength descriptor` 

### Vocal quality descriptor 

This refers to Accent Descriptors where the data contributor refers to their accent using words to describe aspects of their voice that are subjective and qualitative - such as `sultry` or `sassy`. 

* `Vocal quality descriptor` 

TODO: is `quality` the correct word here? 

## Phonetic changes 

This category refers to Accent Descriptors which describe a particular phonetic change. This is used as a parent category to group these Accent Descriptors. 

* `Phonetic changes`

### Specific phonetic changes 

There are several phonetic changes that are linguistic markers for accent difference. 

* `Specified phonetic change` is applied when the Accent Descriptor itself specifies the type of phonetic change. `cot-caught merger` is an example. 

* `Rhoticity` is applied when the Accent Descriptor is describing how `/r/` and related phonemes are pronounced.

* `Inflection` is applied when the Accent Descriptor is describing an inflection change. 

## Register 

Although the Mozilla Common Voice data used _elicited speech_ - utterances spoken from given text prompts, people can speak in a range of _registers_. A register is generally the level of formality of speech - such as `formal`, or `educated` or `slang`. It may indicate socio-economic heritage of the speaker. This category captures Accent Descriptors that describe an accent in this way. 

* `Register` 

## Named accent 

Some accents, such as `Geordie` or `Scouse` have a related geographical region descriptor - North East England, and Liverpool respectively, but ones such as `Received Pronunciation` do not. This category allows for having a Named Accent descriptor where no related geographic region descriptor exists, as well as being able to capture specifically named accents.

* `Named Accent`

## Accent effects due to physical changes 

Accent changes may occur due to physical changes in the speaker's vocal tract - for instance through surgery or disease. This Accent Descriptor is used to capture descriptions such as these. 

* `Accent effects due to physical changes`

## Mixed or variable accent 

Where the data contributor specifies that their accent is a mixture or amalgamation of accents, but does not provide further information (for example so the Accent Descriptors can be separated or merged), this Accent Descriptor is used to capture this description. 

* `Mixed or variable accent`






In [45]:
import cvaccents as cva
#reload(cva)

# Using the Accent Descriptor class to create Accent Descriptor accents for the above 

descriptorGeoRegion = cva.AccentDescriptor(
    id = 100, 
    name='Geographic region', 
    definition = 'Indicates a geographic region used as a descriptor.', 
    parent = None, 
)
descriptorGeoCountry = cva.AccentDescriptor(
    id = 200, 
    name='Country', 
    definition = 'Indicates a geographic region of a country or nation-state.', 
    parent = 100, 
)
descriptorGeoSupra = cva.AccentDescriptor(
    id = 300, 
    name='Supranational region', 
    definition = 'Indicates a geographic region which crosses or overlaps multiple countries.', 
    parent = 100, 
)
descriptorGeoSub = cva.AccentDescriptor(
    id = 400, 
    name='Subnational region', 
    definition = 'Indicates a geographic region within a national boundary.', 
    parent = 100, 
)
descriptorGeoCity = cva.AccentDescriptor(
    id = 500, 
    name='City', 
    definition = 'Indicates a geographic region referring to a city, town or municipality.', 
    parent = 100, 
)

descriptorFOL = cva.AccentDescriptor(
    id = 600, 
    name='First or other language', 
    definition = 'Indicates a descriptor related to whether this is the speaker\s first or other language.', 
    parent = None, 
)
descriptorAccStr = cva.AccentDescriptor(
    id = 700, 
    name='Accent strength descriptor', 
    definition = 'Indicates a marker of accent strength.', 
    parent = None, 
)
descriptorVocQual = cva.AccentDescriptor(
    id = 800, 
    name='Vocal quality descriptor', 
    definition = 'Indicates a subjective vocal quality.', 
    parent = None, 
)
descriptorPhonChanges = cva.AccentDescriptor(
    id = 1000, 
    name='Phonetic Changes', 
    definition = 'Indicates a phonetic change.', 
    parent = None, 
)
descriptorPhonSpecific = cva.AccentDescriptor(
    id = 1100, 
    name='Specific phonetic changes', 
    definition = 'Indicates a specific phonetic change.', 
    parent = 1000, 
)
descriptorPhonRhoticity = cva.AccentDescriptor(
    id = 1200, 
    name='Rhoticity', 
    definition = 'Indicates rhoticity or its absence.', 
    parent = 1000, 
)
descriptorPhonInflection = cva.AccentDescriptor(
    id = 1250, 
    name='Inflection', 
    definition = 'Indicates an inflection change.', 
    parent = 1000, 
)
descriptorRegister = cva.AccentDescriptor(
    id = 1300, 
    name='Register', 
    definition = 'Indicates which register the data contributor speaks in.', 
    parent = None, 
)
descriptorNamedAcc = cva.AccentDescriptor(
    id = 1400, 
    name='Specifically named accent', 
    definition = 'Indicates a specifically named accent.', 
    parent = None, 
)

descriptorPhysChange = cva.AccentDescriptor(
    id = 1500, 
    name='Accent effects due to physical changes', 
    definition = 'Indicates accent changes due to physical changes of the data contributor.', 
    parent = None, 
)
descriptorAccMixed = cva.AccentDescriptor(
    id = 1600, 
    name='Mixed or variable accent', 
    definition = 'Indicates mixture or amalgamation of accents.', 
    parent = None, 
)
descriptorAccUncertainty = cva.AccentDescriptor(
    id = 2000, 
    name='Uncertainty marker', 
    definition = 'Indicates uncertainty of descriptor.', 
    parent = None, 
)



descriptorGeneration = cva.AccentDescriptor(
    id = 2100, 
    name='Generational marker', 
    definition = 'Indicates generational association of speaker.', 
    parent = None, 
)

descriptorSocioeconomic = cva.AccentDescriptor(
    id = 2200, 
    name='Socio-economic marker', 
    definition = 'Indicates the socio-economic status of speaker.', 
    parent = None, 
)

descriptorHybrid = cva.AccentDescriptor(
    id = 2300, 
    name='Hybrid dialect', 
    definition = 'Indicates that the speaker has an accent of a hybrid dialect of the language.', 
    parent = None, 
)
descriptorHeritage = cva.AccentDescriptor(
    id = 2400, 
    name='Linguistic or cultural heritage of speaker', 
    definition = 'Indicates something about the language acquisition or language immersion or cultural heritage of the speaker', 
    parent = None, 
)
descriptorGender = cva.AccentDescriptor(
    id = 2500, 
    name='Gender expression of speaker', 
    definition = 'Indicates the gender expression of the speaker', 
    parent = None, 
)
descriptorReference = cva.AccentDescriptor(
    id = 2600, 
    name='By reference', 
    definition = 'References likeness to the speech of another person', 
    parent = None, 
)


#####

In [46]:
print(descriptorGeoRegion.__str__())
print(descriptorGeoCountry.__str__())
print(descriptorGeoSupra.__str__())
print(descriptorGeoSub.__str__())
print(descriptorGeoCity.__str__())

print(descriptorFOL.__str__())

print(descriptorAccStr.__str__())

print(descriptorVocQual.__str__())

print(descriptorPhonChanges.__str__())
print(descriptorPhonSpecific.__str__())
print(descriptorPhonRhoticity.__str__())
print(descriptorPhonInflection.__str__())

print(descriptorRegister.__str__())

print(descriptorNamedAcc.__str__())

print(descriptorPhysChange.__str__())

print(descriptorAccMixed.__str__())

print(descriptorAccUncertainty.__str__())

print(descriptorGeneration.__str__())

print(descriptorSocioeconomic.__str__())

print(descriptorHybrid.__str__())

print(descriptorHeritage.__str__())

print(descriptorGender.__str__())

print(descriptorReference.__str__())

id is 100, name is Geographic region, definition is Indicates a geographic region used as a descriptor., parent is None
id is 200, name is Country, definition is Indicates a geographic region of a country or nation-state., parent is 100
id is 300, name is Supranational region, definition is Indicates a geographic region which crosses or overlaps multiple countries., parent is 100
id is 400, name is Subnational region, definition is Indicates a geographic region within a national boundary., parent is 100
id is 500, name is City, definition is Indicates a geographic region referring to a city, town or municipality., parent is 100
id is 600, name is First or other language, definition is Indicates a descriptor related to whether this is the speaker\s first or other language., parent is None
id is 700, name is Accent strength descriptor, definition is Indicates a marker of accent strength., parent is None
id is 800, name is Vocal quality descriptor, definition is Indicates a subjective voc

### Now we have the Accent Descriptors defined, we can associate Accent Descriptors with each Accent 

In [47]:
# I could put them all in one list, 
# but it's easier to debug this way

# Generic region descriptors that don't fit into any other category 
region_descriptors = [
]

# Country descriptors 
country_descriptors = [ 
    ('Egyptian', descriptorGeoCountry),
    ('Iraqi', descriptorGeoCountry),
    ('Syrian', descriptorGeoCountry),
    ('Moroccan Arabic', descriptorGeoCountry),
    ('Saudi Arabian', descriptorGeoCountry)
]

# Subnational descriptors 
subnational_descriptors = [
    ('Najdi Arabic', descriptorGeoSub)
]

# Supranational descriptors 
supranational_descriptors = [
    ('North African', descriptorGeoSupra),
    ('Gulf Arabic', descriptorGeoSupra)
]

# City descriptors 
city_descriptors = [
]

# First or other language descriptors 
FOL_descriptors = [
    ('excellent', descriptorFOL),
    ('fluent', descriptorFOL)
]

# Accent Strength descriptors
AccStr_descriptors = [
]


# Vocal quality descriptors
VocQual_descriptors = [
]


# Phonetic descriptors 
PhonSpecific_descriptors = [
]
PhonRhoticity_descriptors = [
]
PhonInflection_descriptors = [
]

# Register descriptors
Register_descriptors = [
]

# Named accent descriptors
NamedAcc_descriptors = [
    ('Modern Standard Arabic - Fusha', descriptorNamedAcc)
]
        
# Physical change descriptors
PhysChange_descriptors = [
    ('nasal breathing issues', descriptorPhysChange)
]

# Mixed accent descriptors
AccMixed_descriptors = [
]
    
# Uncertainty marker 
AccUncertainty_descriptors = [
]    

# Generational associations 
Generation_descriptors = [
]  

# Socio-economic status descriptors 
Socioeconomic_descriptors = [
]

# Hybrid descriptors 
Hybrid_descriptors = [
]

# Heritage descriptors 
Heritage_descriptors = [
]

# Gender descriptors 
Gender_descriptors = [
]

# Reference descriptors 
Reference_descriptors = [
]


In [48]:
# create one list from the above lists 

accent_descriptor_list = [
    region_descriptors,
    country_descriptors,
    subnational_descriptors,
    supranational_descriptors,
    city_descriptors,
    FOL_descriptors,
    AccStr_descriptors,
    VocQual_descriptors,
    PhonSpecific_descriptors,
    PhonRhoticity_descriptors,
    PhonInflection_descriptors,
    Register_descriptors,
    NamedAcc_descriptors,
    PhysChange_descriptors,
    AccMixed_descriptors,
    AccUncertainty_descriptors,
    Generation_descriptors,
    Socioeconomic_descriptors,
    Hybrid_descriptors,
    Heritage_descriptors, 
    Gender_descriptors,
    Reference_descriptors
]



In [49]:
# Now we loop through all the accents 
# And if the accent name matches one of the descriptors in accent_descriptor_list 
# We add the relevant Accent Descriptor to the Accent's object representation 

for accent_descriptor_category in accent_descriptor_list: 
    for accent_descriptor in accent_descriptor_category: 
        for accent in all_accents.items(): 
            
            #print ('accent is: ', accent[1], ' and accent_descriptor is: ', accent_descriptor)
            
            if accent[1]._name == accent_descriptor[0]: 
                #print ('MATCH!')
                if accent[1]._descriptors is None: 
                    accent[1]._descriptors = [] # initialise list if None
                accent[1]._descriptors.append(accent_descriptor[1]) # append because there can be multiple 
                

In [50]:
# the accents should now have descriptors 

import cvaccents as cva
#reload(cva)

#for accent in all_accents.items(): 
    #print(accent[1].__str__())

In [51]:
# Now do a cross-check to see if there are any accents for which the ._descriptor is None 
# this flags if I've missed an accent somewhere 



missing_descriptors = all_accents.reportNoneAccentDescriptors() 

for accent in missing_descriptors: 
    print (accent[1].__str__())
    

## Create relationships between Accents suitable for data visualisation 

Now, we want to create relationships _between_ accents so that we can visualise accents as **nodes** and their relationships as **edges**. 

In [52]:
#pp.pprint(arabic_accents_list)

In [53]:
#for idx, value in all_accents.items(): 
 #   print(idx, value)

In [55]:
## Creating linkages between the individual accents and how they are represented in the data. 
## What I want to do here is create a data structure that has the ID of the accent 
## and something to describe the edge: 
## 
## The data structure I think will work here is: 
## 
## { 99: (123, 456)} 
## to represent an edge between accent ID 123 and accent 456
## 
## One thing to be aware of here is that the edges are NON-DIRECTIONAL
## {99: (123, 456)}
## is equivalent to 
## {99: (123, 456)}
## so we need a way to remove duplicates 

## The data structures we are using are: 
## 
## all_accents - Accent Collection object of all Accents, merged and normalised
## arabic_accents_list - this is a list of list of strings,
##                        where each list represents the Accents that are related
##   
## what we want to do is go through each list, 
## and find the ID number of the accent 
## from the Dict, 
## then build a Dict that represents the Accent's relation to other Accents
## this is accent_nodes

accent_nodes = {}
i = 0;

for accent_list in arabic_accents_list:

    #print(accent_list)
    
    # initialise the list first 
    accent_nodes[i] = []
    
    for accent_list_item in accent_list: 
        #print('now processing', accent_list_item)
        
        for accent in all_accents.items(): 
            
            #if (i%ratio_display ==0): # only show the 100th 
                #print('---')
                #print ('now looking at row: ', accent_list, 'and accent list item: ', accent_list_item, ' and accent: ', accent)
        
            if (accent_list_item == accent[1]._name): ## match 
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('---')
                    #print ('match!')
                    
                #print(accent[0])
                #print('i is: ', i)
                
                
                accent_nodes[i].append(accent[0]) # we want the accent ID number
                
                #if (len(accent_nodes[i]) > 1) : 
                    # double check nodes that have more than 1 element 
                    #print(accent[0])
                    #print('i is: ', i)
                    #print('length of accent_nodes[i] is: ', len(accent_nodes[i]))
                    #pp.pprint(accent_nodes[i])
     
    i +=1                 

In [56]:
pp.pprint(len(accent_nodes))

16


In [57]:
#pp.pprint(accent_nodes)

In [58]:
# this figure is a cross-check - 
# it should equal the original length of accent_nodes minus the size of deletion_list
pp.pprint(len(accent_nodes))

16


In [59]:
#pp.pprint(accent_nodes)

In [60]:
# Now what I need to do is create a JSON format suitable for using in 
# a Trellis diagram in Observable 
# e.g. https://observablehq.com/@jameslaneconkling/trellis

# The format of the JSON looks like: 
#   const nodes = [
#    {id: 'Myriel', group: 1},
#    {id: 'Napoleon', group: 1},

# const edges = [
#    {source: 'Napoleon', target: 'Myriel'},
#    {source: 'Mlle.Baptistine', target: 'Myriel'},

# the nodes should be as easy as JSON dumping the all_accents AccentCollection 
# possibly using a method 

# the edges will be a bit more complex 

### Nodes

In [61]:
#print(all_accents.total())

In [62]:
# use this snippet to find AccentDescriptors that are blank
# which can cause an error in the JSON encoding

for item in all_accents.items(): 
    # the item is an Accent object 
    pp.pprint(item[1].__dict__)
    for descriptor in item[1]._descriptors: 
        pp.pprint(descriptor.__dict__)

{   '_count': 3,
    '_descriptors': [<cvaccents.AccentDescriptor object at 0x7feebe7ca880>],
    '_id': 1,
    '_locale': 'en',
    '_name': 'Syrian',
    '_predetermined': False}
{   '_definition': 'Indicates a geographic region of a country or '
                   'nation-state.',
    '_id': 200,
    '_name': 'Country',
    '_parent': 100}
{   '_count': 7,
    '_descriptors': [<cvaccents.AccentDescriptor object at 0x7feebe7cad60>],
    '_id': 2,
    '_locale': 'en',
    '_name': 'Modern Standard Arabic - Fusha',
    '_predetermined': False}
{   '_definition': 'Indicates a specifically named accent.',
    '_id': 1400,
    '_name': 'Specifically named accent',
    '_parent': None}
{   '_count': 1,
    '_descriptors': [<cvaccents.AccentDescriptor object at 0x7feebe7ca880>],
    '_id': 4,
    '_locale': 'en',
    '_name': 'Moroccan Arabic',
    '_predetermined': False}
{   '_definition': 'Indicates a geographic region of a country or '
                   'nation-state.',
    '_id': 200,

In [63]:
#reload(cva)
all_accents.exportJSON(accents_filename)


is object a Class? False
a
type of object is:  <class 'cvaccents.Accent'>
Accent
Accent
b
does Accent match class name? True
c
does Accent match class qualname? True
d
does Accent match the type of the object? False
e
object for encoding is:  id is 1, name is Syrian, count is 3, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7feebe7ca880>], predetermined is False.
True
True
type of object is:  <class 'cvaccents.Accent'>
Accent
Accent
breakpoint 1
descriptor is:  id is 200, name is Country, definition is Indicates a geographic region of a country or nation-state., parent is 100
is object a Class? False
a
type of object is:  <class 'cvaccents.Accent'>
Accent
Accent
b
does Accent match class name? True
c
does Accent match class qualname? True
d
does Accent match the type of the object? False
e
object for encoding is:  id is 2, name is Modern Standard Arabic - Fusha, count is 7, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7feebe7cad60>], p

True

In [64]:
print(len(accent_nodes))

16


In [65]:
#pp.pprint(accent_nodes)

In [66]:
# let's do some sanity checking to make sure these are correct 

# 0: {'source': 1, 'target': 2, 'weight': 23}
# this is equivalent to the occurrence [1, 2] in accent_nodes 
# plus the occurrences of [2, 1] because we have removed bidirectional edges
# and represents a relationship between 
# 'England English' - accent id 1 - and 'United States English' - accent id 2

print('--- checking 1, 2 ---')

count = 0
for idx, node in accent_nodes.items(): 
    if (node == list([1, 2])) :
        count +=1
print(count)
        
print('--- checking 2, 1 ---')

count = 0
for idx, node in accent_nodes.items(): 
    if (node == list([2, 1])) :
        count +=1
print(count)
        
# these together should sum to 23 
# the first one is 9 which appears correct 
# but the second is 13, not 14 as expected 
# double check the values above. Why do we have an off by one error? 



print ('---')


# 139: {'source': 13016, 'target': 59, 'weight': 2}
# this is equivalent to the occurrence [13016, 59] in accent_nodes
# and represents a relationship between 
# 'Foreign' - accent id 13016 - and 'Non-native speaker'
# this didn't show originally so I dug into it. 
# The original accent listing is: 
# (12775, [750, 13016, 59])

for idx, node in accent_nodes.items(): 
    if node == list([13016, 59]) :
        print ('match')
        
# 

print ('---')

--- checking 1, 2 ---
2
--- checking 2, 1 ---
0
---
---


In [67]:
# So why am I getting an NODE count here of 13, when below I am getting an edge count of 14? 

### Edges

Here, we use the `accent_nodes` dict to create a dict of edges

In [68]:
print(len(accent_nodes))

16


In [69]:
## what we want to do here is loop through the accent_nodes Dict 
## and create another Dict that we can use to create Links between the Nodes (which are accents)

accent_edges = {} 
accent_edges_id = 0


# make a deep copy of accent_nodes as we will be pop()ing elements off lists inside the dict 
# and if we don't make a deep copy this will affect accent_nodes as well 
# because Python uses [pass by assignment](https://docs.python.org/3/faq/programming.html#how-do-i-write-a-function-with-output-parameters-call-by-reference)

accent_nodes_for_manipulation = copy.deepcopy(accent_nodes)

for accent_list in accent_nodes_for_manipulation.items(): 
    #print('\n')
    #print('--- BEGIN accent list ---')
    #print('accent list is: ', accent_list)
    
    if len(accent_list[1]) > 1: 
        #print ('--- node has more than one accent, processing ... ---')       

        # we want to create edges, so only care where the list has two or more elements
        while (len(accent_list[1]) > 1) : 
            
            #print('size of accent_list[1] BEFORE popping is: ', (len(accent_list[1])))
            popped_element = accent_list[1].pop(0) # remove the first element 
            #print('popped element is :', popped_element)
            #print('size of accent_list[1] AFTER popping is: ', (len(accent_list[1])))
    
            # create links between the popped element and all the remaining elements in the list 
            for accent_id in accent_list[1]: 
                
                #print('\n')
                #print('--- in accent list loop ---')
                #print('accent_id is: ', accent_id)
                #print('length of accent list is: ', len(accent_list[1]))
                
                #print('popped_element inside the for loop is: ', popped_element)
                #print('accent_edges_id is: ', accent_edges_id)
                
                accent_edges[accent_edges_id] = {}
                accent_edges[accent_edges_id]['source'] = popped_element
                accent_edges[accent_edges_id]['target'] = accent_id
                accent_edges[accent_edges_id]['weight'] = 1
            
                #print(accent_edges[accent_edges_id])
                
                accent_edges_id +=1
                #print('checking that accent_edges_id has incremented: ', accent_edges_id)
                
            #print('--- END for loop ---')
        #print('--- END while loop ---')       
    #print('--- END accent list ---')


In [70]:
# accent_nodes and accent_nodes_for_manipulation should NOT be equivalent 
# because list items have been pop()'d off the latter

print(len(accent_nodes))
print(len(accent_nodes_for_manipulation))
print (accent_nodes == accent_nodes_for_manipulation)

16
16
False


In [71]:
print(len(accent_edges))

9


In [72]:
#pp.pprint(accent_edges)

In [73]:
print (len(accent_nodes))

16


In [74]:
for idx, node in accent_nodes.items(): 
    # each node is a list 
    if len(node) > 1:
        if (1 in node) and (2 in node): 
            print(node)

[1, 2]
[1, 2]


In [75]:
for idx, node in accent_nodes.items(): 
    # each node is a list 
    if len(node) > 2:
        if (1 in node) and (2 in node): 
            print(node)

In [76]:
for idx, node in accent_nodes.items(): 
    # each node is a list 
    if len(node) == 2:
        if (1 in node) and (2 in node): 
            print(node)

[1, 2]
[1, 2]


This actually returns 30 lines - so we may not have as many _edges_ being generated as there should be. 

There are **11** cases in `accent_nodes` where there are more than two nodes in the list. 

There are **22** cases in `accent_nodes` where there are exactly two nodes in the list. 

_Working hypothesis for this bug:_ I think what's happening here is that the `accent_edges` for nodes with more than 2 nodes are not being generated correctly. 




Now, we de-duplicate the `accent_edges` dict


In [77]:

def deduplicateDict (accent_edges):
    
    temp_edges = []
    temp_dict = {}
    temp_weights = {}

    for key, val in accent_edges.items(): 
        #print (key)
        #print (val)
        
        if val not in temp_edges: 
            
            temp_edges.append(val)
            temp_dict[key] = val 
            temp_weights[key] = 1
            
        else: # increment the weight of the edge
            # find the key to increment based on the val
            #print('breakpoint 1')
            #print ('finding the key to update')
            #pp.pprint(temp_dict)
            #print('breakpoint 2')
            
           # pp.pprint(temp_dict.keys())
            #pp.pprint(temp_dict.values())
            #print('breakpoint 3')
            
            #pp.pprint(key)
            #pp.pprint(val)
            #print('breakpoint 4')
            
            update_key_position = list(temp_dict.values()).index(val) 
            #this is the *position* in the dict that should be updated 
            
            #print('update_key_position is: ', update_key_position)
            
            update_key = list(temp_dict.keys())[update_key_position]

           # print('update_key is: ', update_key)
            
            #print(list(temp_dict.keys()))
            #print('breakpoint 5')
            
            #pp.pprint(temp_dict[update_key])
            temp_weights[update_key] +=1 
            #print('breakpoint 6')
            
    # update the weights - we can't update in the for loop above
    # otherwise the `val` won't match, because the weight: element would be compared
    for key, val in temp_dict.items():
        val['weight'] = temp_weights[key]
        
    #print(type(temp_dict))
    # sort the dict by source because it's easier to do error checking 
    temp_dict = dict(sorted(temp_dict.items(), key=lambda x: x[1]['source'], reverse=False))
    #print(type(temp_dict))
    return temp_dict

In [78]:
accent_edges = deduplicateDict(accent_edges)

    213: {'source': 1287, 'target': 341, 'weight': 1},
    214: {'source': 1287, 'target': 155, 'weight': 1},
    215: {'source': 851, 'target': 341, 'weight': 1},
    216: {'source': 851, 'target': 155, 'weight': 1},
    217: {'source': 341, 'target': 155, 'weight': 1},
    218: {'source': 1, 'target': 1297, 'weight': 1},
    219: {'source': 16, 'target': 132, 'weight': 1},
    222: {'source': 2, 'target': 1297, 'weight': 1},
    223: {'source': 1, 'target': 1544, 'weight': 1},
    224: {'source': 1, 'target': 1550, 'weight': 1},
    225: {'source': 1, 'target': 1551, 'weight': 1},
    226: {'source': 1550, 'target': 1551, 'weight': 1},
    227: {'source': 1, 'target': 1603, 'weight': 1},
    228: {'source': 1, 'target': 1604, 'weight': 1},
    229: {'source': 1603, 'target': 1604, 'weight': 1},
    230: {'source': 245, 'target': 1, 'weight': 1},
    232: {'source': 132, 'target': 8, 'weight': 1},
    234: {'source': 8, 'target': 1941, 'weight': 1},
    235: {'source': 8, 'target': 19

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 1, 'target': 7, 'weight': 1},
    2: {'source': 1, 'target': 31, 'weight': 1},
    3: {'source': 1, 'target': 32, 'weight': 1},
    4: {'source': 1, 'target': 33, 'weight': 1},
    5: {'source': 1, 'target': 34, 'weight': 1},
    6: {'source': 1, 'target': 35, 'weight': 1},
    7: {'source': 1, 'target': 36, 'weight': 1},
    8: {'source': 1, 'target': 37, 'weight': 1},
    9: {'source': 31, 'target': 32, 'weight': 1},
    10: {'source': 31, 'target': 33, 'weight': 1},
    11: {'source': 31, 'target': 34, 'weight': 1},
    12: {'source': 31, 'target': 35, 'weight': 1},
    13: {'source': 31, 'target': 36, 'weight': 1},
    14: {'source': 31, 'target': 37, 'weight': 1},
    15: {'source': 32, 'target': 33, 'weight': 1},
    16: {'source': 32, 'target': 34, 'weight': 1},
    17: {'source': 32, 'target': 35, 'weight': 1},
    18: {'source': 32, 'target': 36, 'weight': 1},
    19: {'source': 32, 'target': 37, 'weight': 1},
 

    119: {'source': 554, 'target': 556, 'weight': 1},
    120: {'source': 554, 'target': 557, 'weight': 1},
    121: {'source': 554, 'target': 558, 'weight': 1},
    122: {'source': 554, 'target': 559, 'weight': 1},
    123: {'source': 554, 'target': 560, 'weight': 1},
    124: {'source': 555, 'target': 556, 'weight': 1},
    125: {'source': 555, 'target': 557, 'weight': 1},
    126: {'source': 555, 'target': 558, 'weight': 1},
    127: {'source': 555, 'target': 559, 'weight': 1},
    128: {'source': 555, 'target': 560, 'weight': 1},
    129: {'source': 556, 'target': 557, 'weight': 1},
    130: {'source': 556, 'target': 558, 'weight': 1},
    131: {'source': 556, 'target': 559, 'weight': 1},
    132: {'source': 556, 'target': 560, 'weight': 1},
    133: {'source': 557, 'target': 558, 'weight': 1},
    134: {'source': 557, 'target': 559, 'weight': 1},
    135: {'source': 557, 'target': 560, 'weight': 1},
    136: {'source': 558, 'target': 559, 'weight': 1},
    137: {'source': 558, 'ta

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 1, 'target': 7, 'weight': 1},
    2: {'source': 1, 'target': 31, 'weight': 1},
    3: {'source': 1, 'target': 32, 'weight': 1},
    4: {'source': 1, 'target': 33, 'weight': 1},
    5: {'source': 1, 'target': 34, 'weight': 1},
    6: {'source': 1, 'target': 35, 'weight': 1},
    7: {'source': 1, 'target': 36, 'weight': 1},
    8: {'source': 1, 'target': 37, 'weight': 1},
    9: {'source': 31, 'target': 32, 'weight': 1},
    10: {'source': 31, 'target': 33, 'weight': 1},
    11: {'source': 31, 'target': 34, 'weight': 1},
    12: {'source': 31, 'target': 35, 'weight': 1},
    13: {'source': 31, 'target': 36, 'weight': 1},
    14: {'source': 31, 'target': 37, 'weight': 1},
    15: {'source': 32, 'target': 33, 'weight': 1},
    16: {'source': 32, 'target': 34, 'weight': 1},
    17: {'source': 32, 'target': 35, 'weight': 1},
    18: {'source': 32, 'target': 36, 'weight': 1},
    19: {'source': 32, 'target': 37, 'weight': 1},
 

    92: {'source': 550, 'target': 559, 'weight': 1},
    93: {'source': 550, 'target': 560, 'weight': 1},
    94: {'source': 551, 'target': 552, 'weight': 1},
    95: {'source': 551, 'target': 553, 'weight': 1},
    96: {'source': 551, 'target': 554, 'weight': 1},
    97: {'source': 551, 'target': 555, 'weight': 1},
    98: {'source': 551, 'target': 556, 'weight': 1},
    99: {'source': 551, 'target': 557, 'weight': 1},
    100: {'source': 551, 'target': 558, 'weight': 1},
    101: {'source': 551, 'target': 559, 'weight': 1},
    102: {'source': 551, 'target': 560, 'weight': 1},
    103: {'source': 552, 'target': 553, 'weight': 1},
    104: {'source': 552, 'target': 554, 'weight': 1},
    105: {'source': 552, 'target': 555, 'weight': 1},
    106: {'source': 552, 'target': 556, 'weight': 1},
    107: {'source': 552, 'target': 557, 'weight': 1},
    108: {'source': 552, 'target': 558, 'weight': 1},
    109: {'source': 552, 'target': 559, 'weight': 1},
    110: {'source': 552, 'target': 5

...

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 1, 'target': 7, 'weight': 1},
    2: {'source': 1, 'target': 31, 'weight': 1},
    3: {'source': 1, 'target': 32, 'weight': 1},
    4: {'source': 1, 'target': 33, 'weight': 1},
    5: {'source': 1, 'target': 34, 'weight': 1},
    6: {'source': 1, 'target': 35, 'weight': 1},
    7: {'source': 1, 'target': 36, 'weight': 1},
    8: {'source': 1, 'target': 37, 'weight': 1},
    9: {'source': 31, 'target': 32, 'weight': 1},
    10: {'source': 31, 'target': 33, 'weight': 1},
    11: {'source': 31, 'target': 34, 'weight': 1},
    12: {'source': 31, 'target': 35, 'weight': 1},
    13: {'source': 31, 'target': 36, 'weight': 1},
    14: {'source': 31, 'target': 37, 'weight': 1},
    15: {'source': 32, 'target': 33, 'weight': 1},
    16: {'source': 32, 'target': 34, 'weight': 1},
    17: {'source': 32, 'target': 35, 'weight': 1},
    18: {'source': 32, 'target': 36, 'weight': 1},
    19: {'source': 32, 'target': 37, 'weight': 1},
 

    329: {'source': 3850, 'target': 3851, 'weight': 1},
    330: {'source': 3850, 'target': 3852, 'weight': 1},
    331: {'source': 3851, 'target': 3852, 'weight': 1},
    332: {'source': 1, 'target': 3904, 'weight': 1},
    337: {'source': 1, 'target': 2998, 'weight': 1},
    339: {'source': 168, 'target': 4280, 'weight': 1},
    342: {'source': 1, 'target': 4606, 'weight': 1},
    346: {'source': 2973, 'target': 5065, 'weight': 1},
    347: {'source': 155, 'target': 5070, 'weight': 1},
    350: {'source': 5114, 'target': 5115, 'weight': 1},
    351: {'source': 13, 'target': 8, 'weight': 1},
    353: {'source': 85, 'target': 3182, 'weight': 1},
    354: {'source': 85, 'target': 988, 'weight': 1},
    358: {'source': 4, 'target': 1, 'weight': 1},
    364: {'source': 851, 'target': 37, 'weight': 1},
    365: {'source': 851, 'target': 182, 'weight': 1},
    366: {'source': 37, 'target': 182, 'weight': 1},
    367: {'source': 5602, 'target': 1, 'weight': 1},
    368: {'source': 5602, 'tar

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 1, 'target': 7, 'weight': 1},
    2: {'source': 1, 'target': 31, 'weight': 1},
    3: {'source': 1, 'target': 32, 'weight': 1},
    4: {'source': 1, 'target': 33, 'weight': 1},
    5: {'source': 1, 'target': 34, 'weight': 1},
    6: {'source': 1, 'target': 35, 'weight': 1},
    7: {'source': 1, 'target': 36, 'weight': 1},
    8: {'source': 1, 'target': 37, 'weight': 1},
    9: {'source': 31, 'target': 32, 'weight': 1},
    10: {'source': 31, 'target': 33, 'weight': 1},
    11: {'source': 31, 'target': 34, 'weight': 1},
    12: {'source': 31, 'target': 35, 'weight': 1},
    13: {'source': 31, 'target': 36, 'weight': 1},
    14: {'source': 31, 'target': 37, 'weight': 1},
    15: {'source': 32, 'target': 33, 'weight': 1},
    16: {'source': 32, 'target': 34, 'weight': 1},
    17: {'source': 32, 'target': 35, 'weight': 1},
    18: {'source': 32, 'target': 36, 'weight': 1},
    19: {'source': 32, 'target': 37, 'weight': 1},
 

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 1, 'target': 7, 'weight': 1},
    2: {'source': 1, 'target': 31, 'weight': 1},
    3: {'source': 1, 'target': 32, 'weight': 1},
    4: {'source': 1, 'target': 33, 'weight': 1},
    5: {'source': 1, 'target': 34, 'weight': 1},
    6: {'source': 1, 'target': 35, 'weight': 1},
    7: {'source': 1, 'target': 36, 'weight': 1},
    8: {'source': 1, 'target': 37, 'weight': 1},
    9: {'source': 31, 'target': 32, 'weight': 1},
    10: {'source': 31, 'target': 33, 'weight': 1},
    11: {'source': 31, 'target': 34, 'weight': 1},
    12: {'source': 31, 'target': 35, 'weight': 1},
    13: {'source': 31, 'target': 36, 'weight': 1},
    14: {'source': 31, 'target': 37, 'weight': 1},
    15: {'source': 32, 'target': 33, 'weight': 1},
    16: {'source': 32, 'target': 34, 'weight': 1},
    17: {'source': 32, 'target': 35, 'weight': 1},
    18: {'source': 32, 'target': 36, 'weight': 1},
    19: {'source': 32, 'target': 37, 'weight': 1},
 

    638: {'source': 1, 'target': 13899, 'weight': 1},
    639: {'source': 5114, 'target': 13910, 'weight': 1},
    640: {'source': 5114, 'target': 182, 'weight': 1},
    641: {'source': 13910, 'target': 182, 'weight': 1},
    642: {'source': 13917, 'target': 40, 'weight': 1},
    644: {'source': 8, 'target': 161, 'weight': 1},
    646: {'source': 8, 'target': 14128, 'weight': 1},
    647: {'source': 8052, 'target': 14128, 'weight': 1},
    648: {'source': 2998, 'target': 85, 'weight': 1},
    649: {'source': 2998, 'target': 13910, 'weight': 1},
    650: {'source': 2998, 'target': 182, 'weight': 1},
    651: {'source': 85, 'target': 13910, 'weight': 1},
    655: {'source': 2742, 'target': 14397, 'weight': 1},
    662: {'source': 245, 'target': 161, 'weight': 1},
    665: {'source': 245, 'target': 6329, 'weight': 1},
    666: {'source': 161, 'target': 9, 'weight': 1},
    667: {'source': 161, 'target': 1, 'weight': 1},
    668: {'source': 161, 'target': 6329, 'weight': 1},
    669: {'sou

In [79]:
#print(type(accent_edges))
#pp.pprint(accent_edges)

In [80]:
# check to see how many duplicates were removed - looks like about 50, or about a quarter
# so it's worth calculating a 'value' for each edge to signify its weight
print(len(accent_edges))

8


### Remove bidirectional edges

Now, we want to deduplicate the **edges** because graph we want to draw is not a _directed graph_. 

That is, the direction of links between nodes is not relevant for the analysis. 

To do this, we compare the `source` and the `target` of each of the edges, and if the `source` and `target` match the `target` and `source` of the edge being compared, we flag that edge for deletion. We then delete those edges flagged for deletion. 

In [81]:

deletion_list = [] # list to keep track of the dict keys that should be deleted 

for edge in accent_edges.items(): 
    #print (node) 
        
    for inner_edge in accent_edges.items(): 
        #pp.pprint(edge)
        #pp.pprint(inner_edge)
            
        # create values to compare on 
        edge_source_target = (edge[1]['source'], edge[1]['target'])
        edge_target_source = (edge[1]['target'], edge[1]['source'])
        inner_edge_target_source = (inner_edge[1]['target'], inner_edge[1]['source'])
        inner_edge_source_target = (inner_edge[1]['source'], inner_edge[1]['target'])
        
        

        if edge_source_target == inner_edge_target_source: # match, remove it 
                
            #print ('match')
            #print(edge_source_target)
            #print(inner_edge_target_source)
                
            # we need to check that the outer edge is not already on the deletion_list 
            # otherwise we end up removing *all* the edges, not just the duplicates 
            
            # we need to also check that the transverse of the outer edge is not already on the deletion_list
            # otherwise we will end up deleting *both* of the edges
            # not just one of them 
            
            if (([inner_edge[0], edge[0]]) not in deletion_list) \
            and (([edge[0], inner_edge[0]]) not in deletion_list) : 
                deletion_list.append([inner_edge[0], edge[0]])
                #print ('added ', ([inner_edge[0], edge[0]]), ' to deletion_list')
            

In [82]:
print (deletion_list)

[]


In [83]:
print (len(deletion_list))

0


In [84]:
# delete the edges in the deletion list, but transfer their weights to the edge that was de-duplicated

for edge_pair in deletion_list: 
    #print(accent_edges[edge_pair[1]])
    #print(accent_edges[edge_pair[0]])
    
    #print('now deleting: ', edge_pair[0])
    
    #print(accent_edges[edge_pair[1]]['weight'])
    #print(accent_edges[edge_pair[0]]['weight'])
    
    
    #print ('now adding weights to: ', edge_pair[1])
    accent_edges[edge_pair[1]]['weight'] += accent_edges[edge_pair[0]]['weight']
    #print(accent_edges[edge_pair[1]]['weight'])
    del accent_edges[edge_pair[0]]
    

In [85]:

print(len(accent_edges)) # this should equal the count before the de-duplication

8


In [86]:
#pp.pprint(accent_edges)

In [87]:
#pp.pprint(accent_nodes)

In [88]:
# let's do some sanity checking to make sure these are correct 

# 0: {'source': 1, 'target': 2, 'weight': 32}
# this is equivalent to the occurrence [1, 2] in accent_nodes 
# plus the occurrences of [2, 1] because we have removed bidirectional edges
# plus any occurrences where 1 or 2 occur in a list, such as [1, 5, 17, 2]
# and represents a relationship between 
# 'England English' - accent id 1 - and 'United States English' - accent id 2

for idx, node in accent_nodes.items(): 
    if (1 in node and 2 in node) :
        print ('match')

print ('---')
print ('there are 32 lines, excellent')
print ('---')


# 5: {'source': 2, 'target': 18, 'weight': 10},

for idx, node in accent_nodes.items(): 
    if (18 in node and 2 in node) :
        print ('match')

print ('---')
print ('there are 10 lines, excellent')
print ('---')

# 64: {'source': 2, 'target': 1325, 'weight': 16}

for idx, node in accent_nodes.items(): 
    if (2 in node and 1325 in node) :
        print ('match')

print ('---')
print ('there are 16 lines, excellent')
print ('---')

match
match
---
there are 32 lines, excellent
---
match
---
there are 10 lines, excellent
---
---
there are 16 lines, excellent
---


In [89]:
# I am now confident that the edges are being represented correctly

In [90]:
# export the edges to a file 

filePath = links_filename

with open(filePath, "w") as outfile:
                json.dump(accent_edges, outfile)

## Some miscellaneous reporting for the paper

I want to get counts by the category of the accent descriptors and the predetermined accents. 

In [91]:
#reload(cva)

predetermined = all_accents.reportPredeterminedAccents()
pp.pprint(predetermined)

[]


In [92]:
#reload (cva) 
accent_category_counts = all_accents.reportAccentDescriptorCategories()
pp.pprint(accent_category_counts)

[   ['Country', 5],
    ['First or other language', 2],
    ['Supranational region', 2],
    ['Specifically named accent', 1],
    ['Accent effects due to physical changes', 1],
    ['Subnational region', 1]]


In [93]:
total = 0
for accent_category_count in accent_category_counts: 
    total+=accent_category_count[1]
    
print (total)

12


In [94]:
#reload (cva) 
accent_multi_descriptor_counts = all_accents.reportMultipleAccentDescriptors()
print(accent_multi_descriptor_counts)

[]


In [95]:
for accent in accent_multi_descriptor_counts: 
    print('\naccent is:', accent[1]._name)
    for descriptor in accent[1]._descriptors: 
        print(descriptor._name)

In [96]:

print(all_accents)

id is 1, name is Syrian, count is 3, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7feebe7ca880>], predetermined is False. id is 2, name is Modern Standard Arabic - Fusha, count is 7, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7feebe7cad60>], predetermined is False. id is 4, name is Moroccan Arabic, count is 1, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7feebe7ca880>], predetermined is False. id is 7, name is excellent, count is 1, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7feebe7caa30>], predetermined is False. id is 8, name is Egyptian, count is 3, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7feebe7ca880>], predetermined is False. id is 9, name is nasal breathing issues, count is 1, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7feebe7cad90>], predetermined is False. id is 12, name is Najdi Arabic, count is 1, locale is en, 